In [2]:
import numpy as np
from datetime import datetime

from strat import RSIRisingFalling

from quantfreedom.enums import *
from quantfreedom.helper_funcs import dl_ex_candles
from quantfreedom.simulate import run_df_backtest, or_backtest


np.set_printoptions(formatter={"float_kind": "{:0.2f}".format})

%load_ext autoreload
%autoreload 2

In [3]:
candles = dl_ex_candles(
    exchange="mufex",
    symbol="BTCUSDT",
    timeframe="15m",
    # candles_to_dl=3000,
    since_datetime=datetime(2023, 1, 1),
    until_datetime=datetime(2024, 2, 29),
)

In [11]:
short_strat = RSIRisingFalling(
    long_short="short",
    rsi_length=np.array([14]),
    rsi_is_above=np.arange(50, 76, 5),
)
short_strat.set_entries_exits_array(
    candles=candles,
    ind_set_index=0,
)
short_strat.plot_signals(candles=candles)

In [4]:
long_strat = RSIRisingFalling(
    long_short="long",
    rsi_length=np.array([14]),
    # default
    rsi_is_below=np.arange(35, 61, 5), #qfscore=0.858 tf 15m gain 252%	
    # test live
    # rsi_is_below=np.arange(34, 56, 5), #qfscore=0.855 tf 15m gain 197%
)
long_strat.set_entries_exits_array(
    candles=candles,
    ind_set_index=2,
)
#long_strat.plot_signals(candles=candles)

In [5]:
backtest_settings = BacktestSettings()

exchange_settings = ExchangeSettings(
    asset_tick_step=3,
    leverage_mode=1,
    leverage_tick_step=2,
    limit_fee_pct=0.0003,
    market_fee_pct=0.0006,
    max_asset_size=100.0,
    max_leverage=150.0,
    min_asset_size=0.001,
    min_leverage=1.0,
    mmr_pct=0.004,
    position_mode=3,
    price_tick_step=1,
)

#default
# static_os = StaticOrderSettings(
#     increase_position_type=IncreasePositionType.RiskPctAccountEntrySize,
#     leverage_strategy_type=LeverageStrategyType.Dynamic,
#     pg_min_max_sl_bcb="min",
#     sl_strategy_type=StopLossStrategyType.SLBasedOnCandleBody,
#     sl_to_be_bool=False,
#     starting_bar=50,
#     starting_equity=1000.0,
#     static_leverage=None,
#     tp_fee_type="limit",
#     tp_strategy_type=TakeProfitStrategyType.RiskReward,
#     trail_sl_bool=True,
#     z_or_e_type=None,
# )

#test live
static_os = StaticOrderSettings(
    increase_position_type=IncreasePositionType.RiskPctAccountEntrySize,
    leverage_strategy_type=LeverageStrategyType.Dynamic,
    pg_min_max_sl_bcb="min",
    sl_strategy_type=StopLossStrategyType.SLBasedOnCandleBody,
    sl_to_be_bool=False,
    starting_bar=50,
    starting_equity=100.0,
    static_leverage=None,
    tp_fee_type="market",
    tp_strategy_type=TakeProfitStrategyType.RiskReward,
    trail_sl_bool=True,
    z_or_e_type=None,
)

# default
# dos_arrays = DynamicOrderSettingsArrays(
#     max_equity_risk_pct=np.array([12]),
#     max_trades=np.array([0]),
#     risk_account_pct_size=np.array([3]),
#     risk_reward=np.array([2, 5]),
#     sl_based_on_add_pct=np.array([0.1, 0.25, 0.5]),
#     sl_based_on_lookback=np.array([20, 50]),
#     sl_bcb_type=np.array([CandleBodyType.Low]),
#     sl_to_be_cb_type=np.array([CandleBodyType.Nothing]),
#     sl_to_be_when_pct=np.array([0]),
#     trail_sl_bcb_type=np.array([CandleBodyType.Low]),
#     trail_sl_by_pct=np.array([0.5, 1.0]),
#     trail_sl_when_pct=np.array([1, 2]),
# )

#test live
dos_arrays = DynamicOrderSettingsArrays(
    max_equity_risk_pct=np.array([5]),
    max_trades=np.array([5]),
    risk_account_pct_size=np.array([3]),
    risk_reward=np.array([2, 5]),
    sl_based_on_add_pct=np.array([0.1, 0.25, 0.5]),
    sl_based_on_lookback=np.array([20, 50]),
    sl_bcb_type=np.array([CandleBodyType.Low]),
    sl_to_be_cb_type=np.array([CandleBodyType.Nothing]),
    sl_to_be_when_pct=np.array([0]),
    trail_sl_bcb_type=np.array([CandleBodyType.Low]),
    trail_sl_by_pct=np.array([0.5, 1.0]),
    trail_sl_when_pct=np.array([1, 2]),
)

In [6]:
backtest_results = run_df_backtest(
    backtest_settings=backtest_settings,
    candles=candles,
    dos_arrays=dos_arrays,
    exchange_settings=exchange_settings,
    static_os=static_os,
    strategy=long_strat,
)

Starting the backtest now ... and also here are some stats for your backtest.

Total indicator settings to test: 5
Total order settings to test: 48
Total combinations of settings to test: 240
Total candles: 24,945
Total candles to test: 5,986,800


In [7]:
backtest_results.sort_values(by=["qf_score","total_pnl"], ascending=False).head(10)

ind_set_idx  dos_index  total_trades  wins  losses  gains_pct  win_rate  \
95             1         47         155.0    60      95    197.628    38.710   
239            4         47         160.0    72      88    258.853    45.000   
191            3         47         163.0    69      94    206.237    42.331   
87             1         39         197.0    60     137    171.661    30.457   
143            2         47         171.0    68     103    172.622    39.766   
215            4         23         158.0    75      83    121.827    47.468   
238            4         46         260.0   127     131    123.595    49.225   
205            4         13         199.0    87     112    112.449    43.719   
91             1         43         162.0    60     102    127.642    37.037   
207            4         15         192.0    84     108    109.329    43.750   

     qf_score  fees_paid  ending_eq  total_pnl  
95      0.855     86.072    297.628    197.628  
239     0.853     62.730    358.853    258.853  
191     0.800     66.393    306.237    206.237  
87      0.789    125.097    271.661    171.661  
143     0.747     69.847    272.622    172.622  
215     0.735     47.199    221.827    121.827  
238     0.718     88.570    223.595    123.595  
205     0.716     68.702    212.449    112.449  
91      0.695     71.436    227.642    127.642  
207     0.695     71.018    209.329    109.329

In [17]:
order_records_df = or_backtest(
    backtest_settings=backtest_settings,
    candles=candles,
    dos_arrays=dos_arrays,
    exchange_settings=exchange_settings,
    static_os=static_os,
    strategy=long_strat,
    dos_index=47,
    ind_set_index=4,
    plot_results=True,
    logger_bool=True,
)

DynamicOrderSettings(
    max_equity_risk_pct = 0.05,
    max_trades = 5,
    risk_account_pct_size = 0.03,
    risk_reward = 5.0,
    sl_based_on_add_pct = 0.005,
    sl_based_on_lookback = 50,
    sl_bcb_type = 3,
    sl_to_be_cb_type = 6,
    sl_to_be_when_pct = 0.0,
    trail_sl_bcb_type = 3,
    trail_sl_by_pct = 0.01,
    trail_sl_when_pct = 0.02,
)
IndicatorSettingsArrays(
    rsi_is_above = nan,
    rsi_is_below = 55.0,
    rsi_length = 14,
)


d:\Lab\quantFreedom\qfstrat\lib\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [13]:
#order_records_df
order_records_df[order_records_df["order_status"] == "StopLossFilled"].sort_values(by=["realized_pnl"], ascending=False).head(10)


ind_set_idx  or_set_idx  bar_idx      timestamp            datetime  \
913            4          47    23607  1707960600000 2024-02-15 01:30:00   
891            4          47    23463  1707831000000 2024-02-13 13:30:00   
611            4          47    18089  1702994400000 2023-12-19 14:00:00   
810            4          47    22118  1706620500000 2024-01-30 13:15:00   
924            4          47    24052  1708361100000 2024-02-19 16:45:00   
786            4          47    21806  1706339700000 2024-01-27 07:15:00   
704            4          47    20051  1704760200000 2024-01-09 00:30:00   
231            4          47     8694  1694538900000 2023-09-12 17:15:00   
461            4          47    15305  1700488800000 2023-11-20 14:00:00   
436            4          47    14872  1700099100000 2023-11-16 01:45:00   

       order_status   equity  available_balance  cash_borrowed  cash_used  \
913  StopLossFilled  307.516            307.516            NaN        NaN   
891  StopLossFilled  282.523            282.523            NaN        NaN   
611  StopLossFilled  212.788            212.788            NaN        NaN   
810  StopLossFilled  235.861            235.861            NaN        NaN   
924  StopLossFilled  312.457            312.457            NaN        NaN   
786  StopLossFilled  228.776            228.776            NaN        NaN   
704  StopLossFilled  243.999            243.999            NaN        NaN   
231  StopLossFilled   94.418             94.418            NaN        NaN   
461  StopLossFilled  179.349            179.349            NaN        NaN   
436  StopLossFilled  177.729            177.729            NaN        NaN   

     ...  entry_size_usd  entry_price  exit_price  position_size_asset  \
913  ...             NaN          NaN     51809.6                  NaN   
891  ...             NaN          NaN     49636.5                  NaN   
611  ...             NaN          NaN     42718.1                  NaN   
810  ...             NaN          NaN     43149.9                  NaN   
924  ...             NaN          NaN     51888.4                  NaN   
786  ...             NaN          NaN     41627.8                  NaN   
704  ...             NaN          NaN     46542.6                  NaN   
231  ...             NaN          NaN     25943.5                  NaN   
461  ...             NaN          NaN     36986.9                  NaN   
436  ...             NaN          NaN     37426.1                  NaN   

     position_size_usd  realized_pnl  sl_pct  sl_price  tp_pct  tp_price  
913                NaN        24.993     NaN       NaN     NaN       NaN  
891                NaN        20.054     NaN       NaN     NaN       NaN  
611                NaN        16.431     NaN       NaN     NaN       NaN  
810                NaN        15.287     NaN       NaN     NaN       NaN  
924                NaN        14.176     NaN       NaN     NaN       NaN  
786                NaN        11.474     NaN       NaN     NaN       NaN  
704                NaN        11.421     NaN       NaN     NaN       NaN  
231                NaN        10.148     NaN       NaN     NaN       NaN  
461                NaN        10.100     NaN       NaN     NaN       NaN  
436                NaN         9.945     NaN       NaN     NaN       NaN  

[10 rows x 27 columns]